In [2]:
import functools
import glob
import itertools
import multiprocessing
import os
import time

import cv2
import numpy
import tensorflow as tf

import common
import mygenerator
import model


def code_to_vec(p, code):
    def char_to_vec(c):
        y = numpy.zeros((len(common.CHARS),))
        y[common.CHARS.index(c)] = 1.0
        return y

    c = numpy.vstack([char_to_vec(c) for c in code])

    return numpy.concatenate([[1. if p else 0], c.flatten()])

In [3]:
def read_data(img_glob):
    for fname in sorted(glob.glob(img_glob)):
        im = cv2.imread(fname)[:, :, 0].astype(numpy.float32) / 255.
        print("read_data:" + fname)
        code = fname.split(os.sep)[1][9:16]
        p = fname.split(os.sep)[1][17] == '1'
        yield im, code_to_vec(p, code)

In [4]:
def unzip(b):
    xs, ys = zip(*b)
    xs = numpy.array(xs)
    ys = numpy.array(ys)
    return xs, ys

In [5]:
def batch(it, batch_size):
    out = []
    for x in it:
        out.append(x)
        if len(out) == batch_size:
            yield out
            out = []
    if out:
        yield out

In [6]:
def mpgen(f):
    def main(q, args, kwargs):
        try:
            for item in f(*args, **kwargs):
                q.put(item)
        finally:
            q.close()

    @functools.wraps(f)
    def wrapped(*args, **kwargs):
        q = multiprocessing.Queue(3)
        proc = multiprocessing.Process(target=main,
                                       args=(q, args, kwargs))
        proc.start()
        try:
            while True:
                item = q.get()
                yield item
        finally:
            proc.terminate()
            proc.join()

    return wrapped

In [7]:
# @mpgen
def read_batches(batch_size):
    g = mygenerator.generate_ims()

    def gen_vecs():
        for im, c, p in itertools.islice(g, batch_size):
            yield im, code_to_vec(p, c)

    while True:
        yield unzip(gen_vecs())

In [8]:
def get_loss(y, y_):
    # Calculate the loss from digits being incorrect.  Don't count loss from
    # digits that are in non-present plates.
    digits_loss = tf.nn.softmax_cross_entropy_with_logits_v2(
        logits=tf.reshape(y[:, 1:],
                          [-1, len(common.CHARS)]),
        labels=tf.reshape(y_[:, 1:],
                          [-1, len(common.CHARS)]))
    digits_loss = tf.reshape(digits_loss, [-1, 7])
    digits_loss = tf.reduce_sum(digits_loss, 1)
    digits_loss *= (y_[:, 0] != 0)
    digits_loss = tf.reduce_sum(digits_loss)

    # Calculate the loss from presence indicator being wrong.
    presence_loss = tf.nn.sigmoid_cross_entropy_with_logits(
        labels=y_[:, :1], logits=y[:, :1])
    presence_loss = 7 * tf.reduce_sum(presence_loss)

    return digits_loss, presence_loss, digits_loss + presence_loss

In [9]:
def train(learn_rate, report_steps, batch_size, initial_weights=None):
    """
    Train the network.
    The function operates interactively: Progress is reported on stdout, and
    training ceases upon `KeyboardInterrupt` at which point the learned weights
    are saved to `weights.npz`, and also returned.
    :param learn_rate:
        Learning rate to use.
    :param report_steps:
        Every `report_steps` batches a progress report is printed.
    :param batch_size:
        The size of the batches used for training.
    :param initial_weights:
        (Optional.) Weights to initialize the network with.
    :return:
        The learned network weights.
    """
    x, y, params = model.get_training_model()

    y_ = tf.placeholder(tf.float32, [None, 7 * len(common.CHARS) + 1])

    digits_loss, presence_loss, loss = get_loss(y, y_)
    train_step = tf.train.AdamOptimizer(learn_rate).minimize(loss)

    best = tf.argmax(tf.reshape(y[:, 1:], [-1, 7, len(common.CHARS)]), 2)
    correct = tf.argmax(tf.reshape(y_[:, 1:], [-1, 7, len(common.CHARS)]), 2)

    if initial_weights is not None:
        assert len(params) == len(initial_weights)
        assign_ops = [w.assign(v) for w, v in zip(params, initial_weights)]

    init = tf.global_variables_initializer()

    def vec_to_plate(v):
        return "".join(common.CHARS[i] for i in v)

    def do_report():
        r = sess.run([best,
                      correct,
                      tf.greater(y[:, 0], 0),
                      y_[:, 0],
                      digits_loss,
                      presence_loss,
                      loss],
                     feed_dict={x: test_xs, y_: test_ys})
        num_correct = numpy.sum(
            numpy.logical_or(
                numpy.all(r[0] == r[1], axis=1),
                numpy.logical_and(r[2] < 0.5,
                                  r[3] < 0.5)))
        r_short = (r[0][:batch_size], r[1][:batch_size], r[2][:batch_size], r[3][:batch_size])
        for b, c, pb, pc in zip(*r_short):
            print("{} {} <-> {} {}".format(vec_to_plate(c), pc,
                                           vec_to_plate(b), float(pb)))
        num_p_correct = numpy.sum(r[2] == r[3])

        print("batch {:3d} correct: {:2.02f}% presence: {:02.02f}% ".format(
            batch_idx, 100. * num_correct / (len(r[0])), 100. * num_p_correct / len(r[2])))
        print("loss: {} (digits: {}, presence: {})".format(r[6], r[4], r[5]))
        print("|{}|".format(
            "".join("X "[numpy.array_equal(b, c) or (not pb and not pc)] for b, c, pb, pc in zip(*r_short))))

    def do_batch():
        sess.run(train_step,
                 feed_dict={x: batch_xs, y_: batch_ys})
        if batch_idx % report_steps == 0:
            do_report()

    #gpu_options = tf.GPUOptions(per_process_gpu_memory_fraction=0.90)  ## OOM:0.6x
    gpu_options = None
    with tf.Session(config=tf.ConfigProto(gpu_options=gpu_options)) as sess:
        sess.run(init)
        if initial_weights is not None:
            sess.run(assign_ops)

        test_xs, test_ys = unzip(list(read_data("test/*.png"))[:batch_size])

        try:
            last_batch_idx = 0
            last_batch_time = time.time()
            batch_iter = enumerate(read_batches(batch_size))
            for batch_idx, (batch_xs, batch_ys) in batch_iter:
                do_batch()
                if batch_idx % report_steps == 0:
                    batch_time = time.time()
                    if last_batch_idx != batch_idx:
                        time_for_batches = (60 * (last_batch_time - batch_time) / (last_batch_idx - batch_idx))
                        print("time for 60 batches {}".format(time_for_batches))
                        print("now: ", time.strftime("%Y-%m-%d %H:%M:%S", time.localtime()))
                        last_batch_idx = batch_idx
                        last_batch_time = batch_time

        except KeyboardInterrupt:
            last_weights = [p.eval() for p in params]
            numpy.savez("CPUweights.npz", *last_weights)
            return last_weights

In [12]:
print("Train start! ", time.strftime("%Y-%m-%d %H:%M:%S", time.localtime()))

weights_fname = "CPUweights.npz"
if weights_fname in os.listdir(os.getcwd()):
    f = numpy.load(weights_fname)
    initial_weights = [f[n] for n in sorted(f.files,
                                            key=lambda s: int(s[4:]))]
else:
    initial_weights = None

train(learn_rate=0.001,
      report_steps=20,
      batch_size=35,
      initial_weights=initial_weights)

print("Train end! ", time.strftime("%Y-%m-%d %H:%M:%S", time.localtime()))

Train start!  2018-09-28 13:57:25
read_data:test/00000000_PG627CN_1.png
read_data:test/00000001_LS152IG_0.png
read_data:test/00000002_VG956EH_1.png
read_data:test/00000003_HC855DA_0.png
read_data:test/00000004_CZ827ZZ_0.png
read_data:test/00000005_PS378BQ_0.png
read_data:test/00000006_JH382II_1.png
read_data:test/00000007_MK637UY_0.png
read_data:test/00000008_RD107HY_0.png
read_data:test/00000009_BG980TJ_0.png
read_data:test/00000010_HQ496RR_0.png
read_data:test/00000011_OS986CQ_1.png
read_data:test/00000012_HM255YH_0.png
read_data:test/00000013_BI974TT_0.png
read_data:test/00000014_XH246AQ_1.png
read_data:test/00000015_KW018OM_1.png
read_data:test/00000016_ET096EC_0.png
read_data:test/00000017_FE378QO_0.png
read_data:test/00000018_SN532NS_0.png
read_data:test/00000019_JH037NW_1.png
read_data:test/00000020_YG310LD_1.png
read_data:test/00000021_VB777RQ_0.png
read_data:test/00000022_QQ575PR_1.png
read_data:test/00000023_GJ329AT_1.png
read_data:test/00000024_QC952QR_0.png
read_data:test/0

read_data:test/00000370_KD324LG_1.png
read_data:test/00000371_NV787ZK_0.png
read_data:test/00000372_QE939YH_1.png
read_data:test/00000373_MZ994HT_0.png
read_data:test/00000374_PC350MF_0.png
read_data:test/00000375_PK157SF_1.png
read_data:test/00000376_MG833JQ_1.png
read_data:test/00000377_RX403WX_0.png
read_data:test/00000378_CK604TO_0.png
read_data:test/00000379_OA916DV_0.png
read_data:test/00000380_RC259QM_1.png
read_data:test/00000381_PW662UJ_1.png
read_data:test/00000382_PL588OD_0.png
read_data:test/00000383_BA472EN_0.png
read_data:test/00000384_WL895GU_0.png
read_data:test/00000385_SJ367UY_1.png
read_data:test/00000386_TJ972IA_0.png
read_data:test/00000387_ND931VV_1.png
read_data:test/00000388_DD889IY_0.png
read_data:test/00000389_CK285OX_1.png
read_data:test/00000390_OH519ZM_0.png
read_data:test/00000391_VD295HX_0.png
read_data:test/00000392_BY335LX_0.png
read_data:test/00000393_KG485TX_1.png
read_data:test/00000394_JK872LP_1.png
read_data:test/00000395_VG628YW_1.png
read_data:te

read_data:test/00000737_JD819QM_0.png
read_data:test/00000738_BS857RR_1.png
read_data:test/00000739_ZZ972BZ_0.png
read_data:test/00000740_KE130GB_0.png
read_data:test/00000741_AA932XR_0.png
read_data:test/00000742_XY777ZQ_1.png
read_data:test/00000743_FJ813YG_1.png
read_data:test/00000744_JN494JM_1.png
read_data:test/00000745_DE534VD_1.png
read_data:test/00000746_DS439AF_0.png
read_data:test/00000747_QL243NJ_0.png
read_data:test/00000748_BT228TE_0.png
read_data:test/00000749_EI692GX_1.png
read_data:test/00000750_IP074OZ_0.png
read_data:test/00000751_SX792FS_0.png
read_data:test/00000752_JS549AW_1.png
read_data:test/00000753_QL504GK_1.png
read_data:test/00000754_LZ054GA_1.png
read_data:test/00000755_YA985NS_0.png
read_data:test/00000756_ZT247BU_1.png
read_data:test/00000757_XJ431DC_0.png
read_data:test/00000758_YP676FH_0.png
read_data:test/00000759_UV600NH_1.png
read_data:test/00000760_QQ192OA_0.png
read_data:test/00000761_GE496VB_0.png
read_data:test/00000762_ST564EA_1.png
read_data:te

read_data:test/00001069_WU935GE_0.png
read_data:test/00001070_QD961JE_0.png
read_data:test/00001071_FC062GX_0.png
read_data:test/00001072_MM997BK_0.png
read_data:test/00001073_KE447XZ_1.png
read_data:test/00001074_OS891HU_0.png
read_data:test/00001075_QG510CK_1.png
read_data:test/00001076_XO346LO_1.png
read_data:test/00001077_YV085NZ_0.png
read_data:test/00001078_AJ508YS_1.png
read_data:test/00001079_LL576PY_0.png
read_data:test/00001080_JS069FX_0.png
read_data:test/00001081_FN126IL_1.png
read_data:test/00001082_XL628MT_1.png
read_data:test/00001083_DY284NY_1.png
read_data:test/00001084_WX353CP_1.png
read_data:test/00001085_SE768PL_0.png
read_data:test/00001086_MO161MX_0.png
read_data:test/00001087_EJ827FS_0.png
read_data:test/00001088_GX787WU_0.png
read_data:test/00001089_FK241DJ_0.png
read_data:test/00001090_VW779NW_1.png
read_data:test/00001091_CJ122WG_1.png
read_data:test/00001092_QY618FN_1.png
read_data:test/00001093_CX728PZ_0.png
read_data:test/00001094_OV004VN_0.png
read_data:te

read_data:test/00001289_IA949CW_0.png
read_data:test/00001290_UW772RU_0.png
read_data:test/00001291_OR419QR_1.png
read_data:test/00001292_RR578RA_1.png
read_data:test/00001293_CZ824RX_0.png
read_data:test/00001294_KE297PD_0.png
read_data:test/00001295_UB074BA_1.png
read_data:test/00001296_OP623EK_0.png
read_data:test/00001297_MY879UP_0.png
read_data:test/00001298_GA332ER_0.png
read_data:test/00001299_QU838AH_1.png
read_data:test/00001300_QT516AF_0.png
read_data:test/00001301_FZ236TO_0.png
read_data:test/00001302_CC319JN_1.png
read_data:test/00001303_QJ250YL_0.png
read_data:test/00001304_QS288MI_0.png
read_data:test/00001305_CH312EV_1.png
read_data:test/00001306_WB825CT_0.png
read_data:test/00001307_DU772CV_0.png
read_data:test/00001308_YR596IK_1.png
read_data:test/00001309_VJ736BI_1.png
read_data:test/00001310_VF900OM_1.png
read_data:test/00001311_YJ973VS_1.png
read_data:test/00001312_FE386VH_1.png
read_data:test/00001313_ZB521TZ_0.png
read_data:test/00001314_EN183UZ_1.png
read_data:te

...

PG627CN 1.0 <-> PG627CN 1.0
LS152IG 0.0 <-> LS152IG 0.0
VG956EH 1.0 <-> VG956EH 1.0
HC855DA 0.0 <-> HC855DA 0.0
CZ827ZZ 0.0 <-> CZ827ZZ 0.0
PS378BQ 0.0 <-> PS378BQ 0.0
JH382II 1.0 <-> JH382II 1.0
MK637UY 0.0 <-> MK637UY 1.0
RD107HY 0.0 <-> RD107HY 0.0
BG980TJ 0.0 <-> BG980TJ 0.0
HQ496RR 0.0 <-> HQ496RY 0.0
OS986CQ 1.0 <-> OS986CQ 1.0
HM255YH 0.0 <-> HM255YH 0.0
BI974TT 0.0 <-> BI974TT 0.0
XH246AQ 1.0 <-> XH246AQ 1.0
KW018OM 1.0 <-> KW018OM 1.0
ET096EC 0.0 <-> ET096ED 0.0
FE378QO 0.0 <-> FE378QO 0.0
SN532NS 0.0 <-> SN532NS 0.0
JH037NW 1.0 <-> JH037NW 1.0
YG310LD 1.0 <-> YG310LD 1.0
VB777RQ 0.0 <-> VB777RQ 0.0
QQ575PR 1.0 <-> QQ575PR 1.0
GJ329AT 1.0 <-> GJ329AT 1.0
QC952QR 0.0 <-> QC952QR 0.0
FH656MC 1.0 <-> FH656MC 1.0
CZ749ZO 0.0 <-> CZ749ZO 0.0
ML037ZN 0.0 <-> MK037ZN 0.0
XV476RF 0.0 <-> XV476RF 0.0
IB777QU 0.0 <-> IB777XT 0.0
QL889AZ 0.0 <-> PL889AZ 0.0
MU884OK 1.0 <-> MU884OK 1.0
EH857YR 0.0 <-> EH857YV 0.0
RB756KU 1.0 <-> RB756KU 1.0
CX335IR 1.0 <-> CX335IR 1.0
batch 101020 correct

PG627CN 1.0 <-> PG627CN 1.0
LS152IG 0.0 <-> LS152IG 0.0
VG956EH 1.0 <-> VG956EH 1.0
HC855DA 0.0 <-> HC855DA 0.0
CZ827ZZ 0.0 <-> CZ827ZZ 0.0
PS378BQ 0.0 <-> US378BQ 0.0
JH382II 1.0 <-> JH382II 1.0
MK637UY 0.0 <-> MK637UY 0.0
RD107HY 0.0 <-> RD107HY 0.0
BG980TJ 0.0 <-> BG980TJ 0.0
HQ496RR 0.0 <-> HQ496RT 0.0
OS986CQ 1.0 <-> OS986CQ 1.0
HM255YH 0.0 <-> HM255YH 0.0
BI974TT 0.0 <-> BI974TT 0.0
XH246AQ 1.0 <-> XH246AQ 1.0
KW018OM 1.0 <-> KW018OM 1.0
ET096EC 0.0 <-> ET096EC 0.0
FE378QO 0.0 <-> FE378QO 0.0
SN532NS 0.0 <-> SN532NS 0.0
JH037NW 1.0 <-> JH037NW 1.0
YG310LD 1.0 <-> YG310LD 1.0
VB777RQ 0.0 <-> VB777RG 0.0
QQ575PR 1.0 <-> QQ575PR 1.0
GJ329AT 1.0 <-> GJ329AT 1.0
QC952QR 0.0 <-> QC952QR 0.0
FH656MC 1.0 <-> FH656MC 1.0
CZ749ZO 0.0 <-> CZ749ZO 0.0
ML037ZN 0.0 <-> MK037ZN 0.0
XV476RF 0.0 <-> XV476RF 1.0
IB777QU 0.0 <-> IB777XT 0.0
QL889AZ 0.0 <-> YL889AZ 0.0
MU884OK 1.0 <-> MU884OK 1.0
EH857YR 0.0 <-> EH857YV 0.0
RB756KU 1.0 <-> RB756KU 1.0
CX335IR 1.0 <-> CX335IR 1.0
batch 101160 correct

PG627CN 1.0 <-> PG627CN 1.0
LS152IG 0.0 <-> LS152IG 0.0
VG956EH 1.0 <-> VG956EH 1.0
HC855DA 0.0 <-> HC855DA 0.0
CZ827ZZ 0.0 <-> CZ827ZZ 0.0
PS378BQ 0.0 <-> HS398BQ 0.0
JH382II 1.0 <-> JH382II 1.0
MK637UY 0.0 <-> MK637UY 1.0
RD107HY 0.0 <-> RD107HY 0.0
BG980TJ 0.0 <-> BG980TJ 0.0
HQ496RR 0.0 <-> HQ496KR 0.0
OS986CQ 1.0 <-> OS986CQ 1.0
HM255YH 0.0 <-> HM255YH 0.0
BI974TT 0.0 <-> BI974TT 0.0
XH246AQ 1.0 <-> XH246AQ 1.0
KW018OM 1.0 <-> KW018OM 1.0
ET096EC 0.0 <-> ET096EC 0.0
FE378QO 0.0 <-> FE378QO 0.0
SN532NS 0.0 <-> SN532NS 0.0
JH037NW 1.0 <-> JH037NW 1.0
YG310LD 1.0 <-> YG310LD 1.0
VB777RQ 0.0 <-> VB777RJ 0.0
QQ575PR 1.0 <-> QQ575PR 1.0
GJ329AT 1.0 <-> GJ329AT 1.0
QC952QR 0.0 <-> QC952QR 0.0
FH656MC 1.0 <-> FH656MC 1.0
CZ749ZO 0.0 <-> CZ749ZO 0.0
ML037ZN 0.0 <-> ML037ZN 0.0
XV476RF 0.0 <-> XV476RF 0.0
IB777QU 0.0 <-> IB777XT 0.0
QL889AZ 0.0 <-> OL889AZ 0.0
MU884OK 1.0 <-> MU884OK 1.0
EH857YR 0.0 <-> EH857VV 0.0
RB756KU 1.0 <-> RB756KU 1.0
CX335IR 1.0 <-> CX335IR 1.0
batch 101300 correct

PG627CN 1.0 <-> PG627CN 1.0
LS152IG 0.0 <-> LS152IG 0.0
VG956EH 1.0 <-> VG956EH 1.0
HC855DA 0.0 <-> HC855DA 0.0
CZ827ZZ 0.0 <-> CZ827ZZ 0.0
PS378BQ 0.0 <-> US378BQ 0.0
JH382II 1.0 <-> JH382II 1.0
MK637UY 0.0 <-> MK637UY 1.0
RD107HY 0.0 <-> RD107HY 0.0
BG980TJ 0.0 <-> BG980TJ 0.0
HQ496RR 0.0 <-> HQ496RR 0.0
OS986CQ 1.0 <-> OS986CQ 1.0
HM255YH 0.0 <-> HM255YH 0.0
BI974TT 0.0 <-> BI974TT 0.0
XH246AQ 1.0 <-> XH246AQ 1.0
KW018OM 1.0 <-> KW018OM 1.0
ET096EC 0.0 <-> ET096EC 0.0
FE378QO 0.0 <-> FE378QO 0.0
SN532NS 0.0 <-> SN532NS 0.0
JH037NW 1.0 <-> JH037NW 1.0
YG310LD 1.0 <-> YG310LD 1.0
VB777RQ 0.0 <-> VB777RQ 0.0
QQ575PR 1.0 <-> QQ575PR 1.0
GJ329AT 1.0 <-> GJ329AT 1.0
QC952QR 0.0 <-> QC952QR 0.0
FH656MC 1.0 <-> FH656MC 1.0
CZ749ZO 0.0 <-> CZ749ZO 0.0
ML037ZN 0.0 <-> ML037ZN 0.0
XV476RF 0.0 <-> XV476RF 1.0
IB777QU 0.0 <-> IB777XT 0.0
QL889AZ 0.0 <-> KL889AZ 0.0
MU884OK 1.0 <-> MU884OK 1.0
EH857YR 0.0 <-> EH857VV 0.0
RB756KU 1.0 <-> RB756KU 1.0
CX335IR 1.0 <-> CX335IR 1.0
batch 101440 correct

PG627CN 1.0 <-> PG627CN 1.0
LS152IG 0.0 <-> LS152IG 0.0
VG956EH 1.0 <-> VG956EH 1.0
HC855DA 0.0 <-> HC855DA 0.0
CZ827ZZ 0.0 <-> CZ827ZZ 0.0
PS378BQ 0.0 <-> US378BQ 0.0
JH382II 1.0 <-> JH382II 1.0
MK637UY 0.0 <-> MK637UY 1.0
RD107HY 0.0 <-> RD107HY 0.0
BG980TJ 0.0 <-> BG980TJ 0.0
HQ496RR 0.0 <-> HQ296RR 0.0
OS986CQ 1.0 <-> OS986CQ 1.0
HM255YH 0.0 <-> HW255YW 0.0
BI974TT 0.0 <-> BI974TT 0.0
XH246AQ 1.0 <-> XH246AQ 1.0
KW018OM 1.0 <-> KW018OM 1.0
ET096EC 0.0 <-> ET096EC 0.0
FE378QO 0.0 <-> FE378QO 0.0
SN532NS 0.0 <-> SN532NS 0.0
JH037NW 1.0 <-> JH037NW 1.0
YG310LD 1.0 <-> YG310LD 1.0
VB777RQ 0.0 <-> VB777RJ 0.0
QQ575PR 1.0 <-> QQ575PR 1.0
GJ329AT 1.0 <-> GJ329AT 1.0
QC952QR 0.0 <-> QC952QR 0.0
FH656MC 1.0 <-> FH656MC 1.0
CZ749ZO 0.0 <-> CZ749ZO 0.0
ML037ZN 0.0 <-> ME037ZN 0.0
XV476RF 0.0 <-> XV476RF 0.0
IB777QU 0.0 <-> IB777XT 0.0
QL889AZ 0.0 <-> NL889AZ 0.0
MU884OK 1.0 <-> MU884OK 1.0
EH857YR 0.0 <-> EH857YC 0.0
RB756KU 1.0 <-> RB756KU 1.0
CX335IR 1.0 <-> CX335IR 1.0
batch 101580 correct